### Apriori
Apriori原理是说如果某个项集是频繁的，那么它的所有子集也是频繁的。这个原理直观上并没有什么帮助，但是如果反过来看就有用了，也就是说如果一个项集是非频繁集，那么它的所有超集也是非频繁的。 

### 生成候选项集
```
对数据集中的每条交易记录tran:
    对每个候选项集can:
        检查一下can是否是tran的子集:
            如果是，则增加can的计数值

对每个候选项集:
    如果其支持度不低于最小值，则保留该项集

返回所有频繁项集列表
```

### 组织完整的Apriori算法
```
当集合中项的个数大于0时:
    构建一个k个项组成的候选项集的列表
    检查数据以确认每个项集都是频繁的
    保留频繁项集并构建k+1项组成的候选项集的列表
```

In [1]:
# 对C1中每个项构建一个不变集合
def createC1(dataSet):
    C1 = []
    for transaction in dataSet:  # 对数据集中的每条交易记录tran
        for item in transaction:  # 对每个候选项集can
            if not [item] in C1:  # 检查一下can是否是tran的子集
                C1.append([item])  # 如果是，则增加can的计数值
    C1.sort()
    return list(map(frozenset, C1))

# 计算所有项集的支持度
def scanD(D, Ck, minSupport):
    ssCnt = {}
    for tid in D:
        for can in Ck:
            if can.issubset(tid):
                if not can in ssCnt:
                    ssCnt[can] = 1
                else:
                    ssCnt[can] += 1
    numItems = float(len(D))
    retList = []
    supportData = {}
    for key in ssCnt:  # 对每个候选项集
        support = ssCnt[key] / numItems
        if support >= minSupport:  # 如果其支持度不低于最小值，则保留该项集
            retList.insert(0, key)
        supportData[key] = support
    return retList, supportData  # 返回所有频繁项集列表

In [2]:
def aprioriGen(Lk, k):
    retList = []
    lenLk = len(Lk)
    for i in range(lenLk):
        for j in range(i + 1, lenLk):
            L1 = list(Lk[i])[:k - 2];
            L2 = list(Lk[j])[:k - 2]
            L1.sort();
            L2.sort()
            if L1 == L2:  # 前k-2个项相同时，将两个集合合并
                retList.append(Lk[i] | Lk[j])
    return retList

def apriori(dataSet, minSupport=0.5):
    C1 = createC1(dataSet)
    D = list(map(set, dataSet))
    L1, supportData = scanD(D, C1, minSupport)
    L = [L1]
    k = 2
    # 扫描数据集，从Ck得到Lk
    while (len(L[k - 2]) > 0):  # 当集合中项的个数大于0时:
        Ck = aprioriGen(L[k - 2], k)  # 构建一个k个项组成的候选项集的列表
        Lk, supK = scanD(D, Ck, minSupport)  # 检查数据以确认每个项集都是频繁的
        supportData.update(supK)  # 保留频繁项集并构建k+1项组成的候选项集的列表
        L.append(Lk)
        k += 1
    return L, supportData

In [3]:
# 生成关联规则
def generateRules(L, supportData, minConf=0.7):
    bigRuleList = []
    for i in range(1, len(L)):  # 只获取有两个或更多元素的集合
        for freqSet in L[i]:
            H1 = [frozenset([item]) for item in freqSet]
            if (i > 1):
                rulesFromConseq(freqSet, H1, supportData, bigRuleList, minConf)
            else:
                calcConf(freqSet, H1, supportData, bigRuleList, minConf)
    return bigRuleList

# 生成候选规则集合
def calcConf(freqSet, H, supportData, brl, minConf=0.7):
    prunedH = []
    for conseq in H:  # 遍历H中的所有项集并计算它们的可信度值
        conf = supportData[freqSet] / supportData[freqSet - conseq]
        if conf >= minConf:
            # print (freqSet-conseq, '-->', conseq, 'conf:', conf)
            brl.append((freqSet - conseq, conseq, conf))
            prunedH.append(conseq)
    return prunedH

# 对规则进行评估
def rulesFromConseq(freqSet, H, supportData, brl, minConf=0.7):
    m = len(H[0])
    if (len(freqSet) > (m + 1)):  # 尝试进一步合并
        Hmp1 = aprioriGen(H, m + 1)  # 创建Hm+1条新候选规则
        Hmp1 = calcConf(freqSet, Hmp1, supportData, brl, minConf)
        if (len(Hmp1) > 1):
            rulesFromConseq(freqSet, Hmp1, supportData, brl, minConf)

### 毒蘑菇数据集
数据集中包含了8124个样本和22个变量（如蘑菇的颜色、形状、光滑度等）。

每一种都被分为绝对可食用的，绝对有毒的，或者具有未知的可食性。

该数据集是探究机器学习分类算法算法不可多得的一个优质数据集。

parameters:
```
cap-shape: bell=b,conical=c,convex=x,flat=f, knobbed=k,sunken=s
cap-surface: fibrous=f,grooves=g,scaly=y,smooth=s
cap-color: brown=n,buff=b,cinnamon=c,gray=g,green=r,pink=p,purple=u,red=e,white=w,yellow=y
bruises: bruises=t,no=f
odor: almond=a,anise=l,creosote=c,fishy=y,foul=f,musty=m,none=n,pungent=p,spicy=s
gill-attachment: attached=a,descending=d,free=f,notched=n
gill-spacing: close=c,crowded=w,distant=d
gill-size: broad=b,narrow=n
gill-color: black=k,brown=n,buff=b,chocolate=h,gray=g, green=r,orange=o,pink=p,purple=u,red=e,white=w,yellow=y
stalk-shape: enlarging=e,tapering=t
stalk-root: bulbous=b,club=c,cup=u,equal=e,rhizomorphs=z,rooted=r,missing=?
stalk-surface-above-ring: fibrous=f,scaly=y,silky=k,smooth=s
stalk-surface-below-ring: fibrous=f,scaly=y,silky=k,smooth=s
stalk-color-above-ring: brown=n,buff=b,cinnamon=c,gray=g,orange=o,pink=p,red=e,white=w,yellow=y
stalk-color-below-ring: brown=n,buff=b,cinnamon=c,gray=g,orange=o,pink=p,red=e,white=w,yellow=y
veil-type: partial=p,universal=u
veil-color: brown=n,orange=o,white=w,yellow=y
ring-number: none=n,one=o,two=t
ring-type: cobwebby=c,evanescent=e,flaring=f,large=l,none=n,pendant=p,sheathing=s,zone=z
spore-print-color: black=k,brown=n,buff=b,chocolate=h,green=r,orange=o,purple=u,white=w,yellow=y
population: abundant=a,clustered=c,numerous=n,scattered=s,several=v,solitary=y
habitat: grasses=g,leaves=l,meadows=m,paths=p,urban=u,waste=w,woods=d
```

examples:
```
1 3 9 13 23 25 34 36 38 40 52 54 59 63 67 76 85 86 90 93 98 107 113 
2 3 9 14 23 26 34 36 39 40 52 55 59 63 67 76 85 86 90 93 99 108 114 
2 4 9 15 23 27 34 36 39 41 52 55 59 63 67 76 85 86 90 93 99 108 115 
```

In [4]:
mushDataSet = [line.split() for line in open('data/mushroom.dat').readlines()]

In [5]:
L, suppData = apriori(mushDataSet, minSupport=0.3)
rules = generateRules(L, suppData, minConf=0.3)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'28'}) --> frozenset({'2'}) conf: 0.9659863945578231
frozenset({'53'}) --> frozenset({'2'}) conf: 0.5625
frozenset({'23'}) --> frozenset({'2'}) conf: 0.8151658767772512
frozenset({'34'}) --> frozenset({'2'}) conf: 0.5074551427849381
frozenset({'36'}) --> frozenset({'2'}) conf: 0.44157369348209047
frozenset({'59'}) --> frozenset({'2'}) conf: 0.7032457496136012
frozenset({'63'}) --> frozenset({'2'}) conf: 0.6888168557536466
frozenset({'67'}) --> frozenset({'2'}) conf: 0.6164874551971327
frozenset({'76'}) --> frozenset({'2'}) conf: 0.6167883211678832
frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
frozenset({'86'}) --> frozenset({'2'}) conf: 0.5068147400302877
frozenset({'90'}) --> frozenset({'2'}) conf: 0.4914529914529915
frozenset({'93'}) --> frozenset({'2'}) conf: 0.7943548387096774
frozenset({'39'}) --> frozenset({'2'}) conf: 0.6985032074126871
frozenset({'53'}) --> frozenset({'39', '2'}) conf: 0.5416666666666666
frozenset({'39'}) --> frozenset({'53', '2'}) c

frozenset({'86'}) --> frozenset({'34', '67', '2'}) conf: 0.34729934376577487
frozenset({'67'}) --> frozenset({'34', '86', '2'}) conf: 0.6164874551971327
frozenset({'34'}) --> frozenset({'86', '67', '2'}) conf: 0.34773818549406116
frozenset({'34', '36'}) --> frozenset({'90', '2'}) conf: 0.3901847924871251
frozenset({'34', '90'}) --> frozenset({'2', '36'}) conf: 0.35307017543859653
frozenset({'90', '36'}) --> frozenset({'34', '2'}) conf: 0.39851485148514854
frozenset({'34'}) --> frozenset({'90', '2', '36'}) conf: 0.325499115491534
frozenset({'36'}) --> frozenset({'34', '90', '2'}) conf: 0.3781561949500881
frozenset({'90'}) --> frozenset({'34', '2', '36'}) conf: 0.344017094017094
frozenset({'34', '59'}) --> frozenset({'90', '2'}) conf: 0.6179775280898877
frozenset({'90', '59'}) --> frozenset({'34', '2'}) conf: 0.6503378378378379
frozenset({'34', '90'}) --> frozenset({'59', '2'}) conf: 0.42214912280701755
frozenset({'34'}) --> frozenset({'90', '59', '2'}) conf: 0.38918372504422544
frozense

frozenset({'34', '90'}) --> frozenset({'53', '85', '2'}) conf: 0.35526315789473684
frozenset({'34', '85'}) --> frozenset({'90', '53', '2'}) conf: 0.3275208491281274
frozenset({'53', '85'}) --> frozenset({'34', '90', '2'}) conf: 0.5625
frozenset({'90', '85'}) --> frozenset({'34', '53', '2'}) conf: 0.34615384615384615
frozenset({'34'}) --> frozenset({'90', '2', '53', '85'}) conf: 0.3275208491281274
frozenset({'53'}) --> frozenset({'90', '2', '34', '85'}) conf: 0.5625
frozenset({'90'}) --> frozenset({'2', '34', '53', '85'}) conf: 0.34615384615384615
frozenset({'85'}) --> frozenset({'90', '2', '34', '53'}) conf: 0.3190546528803545
frozenset({'34', '53', '86'}) --> frozenset({'85', '2'}) conf: 0.5625
frozenset({'53', '85', '86'}) --> frozenset({'34', '2'}) conf: 0.5625
frozenset({'34', '85', '86'}) --> frozenset({'53', '2'}) conf: 0.3278522641032128
frozenset({'34', '53', '85'}) --> frozenset({'86', '2'}) conf: 0.5625
frozenset({'34', '53'}) --> frozenset({'86', '85', '2'}) conf: 0.5625
fro

frozenset({'85', '86'}) --> frozenset({'34', '39', '2'}) conf: 0.47046945986875316
frozenset({'34', '39'}) --> frozenset({'86', '85', '2'}) conf: 0.690114772306553
frozenset({'39', '86'}) --> frozenset({'34', '85', '2'}) conf: 0.6878228782287823
frozenset({'39', '85'}) --> frozenset({'34', '86', '2'}) conf: 0.6642908054169637
frozenset({'34'}) --> frozenset({'2', '39', '85', '86'}) conf: 0.4710639373262573
frozenset({'86'}) --> frozenset({'2', '34', '39', '85'}) conf: 0.47046945986875316
frozenset({'85'}) --> frozenset({'2', '34', '39', '86'}) conf: 0.4588872476612506
frozenset({'39'}) --> frozenset({'2', '34', '85', '86'}) conf: 0.6642908054169637
frozenset({'34', '59', '86'}) --> frozenset({'39', '2'}) conf: 0.6388443017656501
frozenset({'34', '39', '86'}) --> frozenset({'59', '2'}) conf: 0.5894113291373565
frozenset({'39', '59', '86'}) --> frozenset({'34', '2'}) conf: 0.9364705882352942
frozenset({'34', '39', '59'}) --> frozenset({'86', '2'}) conf: 0.9364705882352942
frozenset({'34'

frozenset({'63'}) --> frozenset({'93', '2', '39', '59'}) conf: 0.5137763371150729
frozenset({'59'}) --> frozenset({'93', '2', '63', '39'}) conf: 0.4899536321483771
frozenset({'39'}) --> frozenset({'93', '2', '63', '59'}) conf: 0.4518888096935139
frozenset({'93'}) --> frozenset({'2', '63', '39', '59'}) conf: 0.6391129032258064
frozenset({'63', '59', '86'}) --> frozenset({'93', '2'}) conf: 0.639757820383451
frozenset({'63', '93', '86'}) --> frozenset({'59', '2'}) conf: 0.773170731707317
frozenset({'59', '93', '86'}) --> frozenset({'63', '2'}) conf: 0.7304147465437788
frozenset({'63', '59', '93'}) --> frozenset({'86', '2'}) conf: 0.7620192307692307
frozenset({'63', '86'}) --> frozenset({'59', '93', '2'}) conf: 0.5345699831365937
frozenset({'63', '59'}) --> frozenset({'86', '93', '2'}) conf: 0.6102021174205967
frozenset({'59', '86'}) --> frozenset({'63', '93', '2'}) conf: 0.5088282504012841
frozenset({'63', '93'}) --> frozenset({'86', '59', '2'}) conf: 0.7304147465437788
frozenset({'93', '

...

frozenset({'23'}) --> frozenset({'85', '2', '36', '34', '63', '86'}) conf: 0.7298578199052134
frozenset({'85'}) --> frozenset({'23', '2', '36', '34', '63', '86'}) conf: 0.3032988675529296
frozenset({'59', '23', '36', '34', '86'}) --> frozenset({'93', '2'}) conf: 0.7877237851662405
frozenset({'93', '23', '36', '34', '86'}) --> frozenset({'59', '2'}) conf: 0.8
frozenset({'93', '59', '36', '34', '86'}) --> frozenset({'23', '2'}) conf: 0.7877237851662405
frozenset({'93', '59', '23', '34', '86'}) --> frozenset({'2', '36'}) conf: 0.8105263157894738
frozenset({'93', '59', '23', '36', '86'}) --> frozenset({'34', '2'}) conf: 0.8392370572207085
frozenset({'93', '59', '23', '36', '34'}) --> frozenset({'86', '2'}) conf: 0.8392370572207085
frozenset({'34', '23', '86', '36'}) --> frozenset({'59', '93', '2'}) conf: 0.7530562347188264
frozenset({'34', '59', '86', '36'}) --> frozenset({'23', '93', '2'}) conf: 0.5822306238185256
frozenset({'34', '23', '59', '86'}) --> frozenset({'93', '2', '36'}) conf: 

frozenset({'34', '63', '59'}) --> frozenset({'23', '2', '36', '86'}) conf: 0.6215943491422806
frozenset({'63', '59', '86'}) --> frozenset({'23', '2', '36', '34'}) conf: 0.6215943491422806
frozenset({'59', '86', '36'}) --> frozenset({'23', '2', '34', '63'}) conf: 0.5822306238185256
frozenset({'63', '59', '36'}) --> frozenset({'23', '2', '34', '86'}) conf: 0.6695652173913044
frozenset({'34', '59', '86'}) --> frozenset({'23', '2', '36', '63'}) conf: 0.49438202247191015
frozenset({'34', '59', '36'}) --> frozenset({'23', '2', '63', '86'}) conf: 0.5822306238185256
frozenset({'23', '59', '86'}) --> frozenset({'2', '36', '34', '63'}) conf: 0.7623762376237625
frozenset({'23', '59', '36'}) --> frozenset({'2', '34', '63', '86'}) conf: 0.7877237851662405
frozenset({'63', '23', '59'}) --> frozenset({'2', '36', '34', '86'}) conf: 0.8301886792452832
frozenset({'34', '23', '59'}) --> frozenset({'2', '36', '63', '86'}) conf: 0.7623762376237625
frozenset({'34', '63'}) --> frozenset({'59', '23', '2', '36

frozenset({'39', '23', '36', '34', '86'}) --> frozenset({'63', '85', '2'}) conf: 0.8169761273209549
frozenset({'39', '85', '34', '63', '86'}) --> frozenset({'23', '2', '36'}) conf: 0.7680798004987532
frozenset({'39', '85', '36', '34', '63'}) --> frozenset({'23', '86', '2'}) conf: 0.9194029850746269
frozenset({'39', '85', '36', '63', '86'}) --> frozenset({'34', '23', '2'}) conf: 0.9194029850746269
frozenset({'39', '85', '36', '34', '86'}) --> frozenset({'63', '23', '2'}) conf: 0.5669581224114129
frozenset({'39', '85', '23', '63', '86'}) --> frozenset({'34', '2', '36'}) conf: 0.9194029850746269
frozenset({'39', '85', '23', '36', '86'}) --> frozenset({'34', '63', '2'}) conf: 0.8169761273209549
frozenset({'39', '85', '23', '36', '63'}) --> frozenset({'34', '86', '2'}) conf: 0.9194029850746269
frozenset({'39', '85', '23', '34', '86'}) --> frozenset({'63', '2', '36'}) conf: 0.8169761273209549
frozenset({'39', '85', '23', '36', '34'}) --> frozenset({'63', '86', '2'}) conf: 0.8169761273209549


frozenset({'34', '23', '93'}) --> frozenset({'39', '59', '2', '36', '86'}) conf: 0.7738693467336684
frozenset({'34', '93', '36'}) --> frozenset({'39', '59', '23', '2', '86'}) conf: 0.7493917274939174
frozenset({'34', '93', '86'}) --> frozenset({'39', '59', '23', '2', '36'}) conf: 0.652542372881356
frozenset({'34', '59', '93'}) --> frozenset({'39', '23', '2', '36', '86'}) conf: 0.7096774193548387
frozenset({'59', '93', '86'}) --> frozenset({'39', '23', '2', '36', '34'}) conf: 0.7096774193548387
frozenset({'23', '93', '36'}) --> frozenset({'39', '59', '2', '34', '86'}) conf: 0.8
frozenset({'93', '86', '36'}) --> frozenset({'39', '59', '23', '2', '34'}) conf: 0.7493917274939174
frozenset({'59', '93', '36'}) --> frozenset({'39', '23', '2', '34', '86'}) conf: 0.7421686746987953
frozenset({'23', '93', '86'}) --> frozenset({'39', '59', '2', '36', '34'}) conf: 0.7738693467336684
frozenset({'23', '59', '93'}) --> frozenset({'39', '2', '36', '34', '86'}) conf: 0.8105263157894738
frozenset({'34',

frozenset({'34', '39', '59', '63'}) --> frozenset({'2', '36', '85', '86'}) conf: 0.8579387186629528
frozenset({'34', '39', '59', '86'}) --> frozenset({'2', '36', '63', '85'}) conf: 0.7247058823529413
frozenset({'34', '39', '59', '36'}) --> frozenset({'2', '63', '85', '86'}) conf: 0.8579387186629528
frozenset({'39', '59', '85', '86'}) --> frozenset({'2', '36', '34', '63'}) conf: 0.7247058823529413
frozenset({'39', '59', '85', '36'}) --> frozenset({'2', '34', '63', '86'}) conf: 0.8041775456919061
frozenset({'63', '39', '59', '85'}) --> frozenset({'2', '36', '34', '86'}) conf: 0.8041775456919061
frozenset({'34', '39', '59', '85'}) --> frozenset({'2', '36', '63', '86'}) conf: 0.7247058823529413
frozenset({'34', '63', '36'}) --> frozenset({'39', '59', '85', '2', '86'}) conf: 0.6172344689378758
frozenset({'34', '63', '86'}) --> frozenset({'39', '59', '85', '2', '36'}) conf: 0.5193929173693087
frozenset({'34', '63', '85'}) --> frozenset({'39', '59', '2', '36', '86'}) conf: 0.5193929173693087


In [6]:
L, suppData = apriori(mushDataSet, minSupport=0.3)
rules = generateRules(L, suppData, minConf=0.4)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'28'}) --> frozenset({'2'}) conf: 0.9659863945578231
frozenset({'53'}) --> frozenset({'2'}) conf: 0.5625
frozenset({'23'}) --> frozenset({'2'}) conf: 0.8151658767772512
frozenset({'34'}) --> frozenset({'2'}) conf: 0.5074551427849381
frozenset({'36'}) --> frozenset({'2'}) conf: 0.44157369348209047
frozenset({'59'}) --> frozenset({'2'}) conf: 0.7032457496136012
frozenset({'63'}) --> frozenset({'2'}) conf: 0.6888168557536466
frozenset({'67'}) --> frozenset({'2'}) conf: 0.6164874551971327
frozenset({'76'}) --> frozenset({'2'}) conf: 0.6167883211678832
frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
frozenset({'86'}) --> frozenset({'2'}) conf: 0.5068147400302877
frozenset({'90'}) --> frozenset({'2'}) conf: 0.4914529914529915
frozenset({'93'}) --> frozenset({'2'}) conf: 0.7943548387096774
frozenset({'39'}) --> frozenset({'2'}) conf: 0.6985032074126871
frozenset({'53'}) --> frozenset({'39', '2'}) conf: 0.5416666666666666
frozenset({'39'}) --> frozenset({'53', '2'}) c

frozenset({'63'}) --> frozenset({'34', '85', '2'}) conf: 0.6499189627228524
frozenset({'34'}) --> frozenset({'63', '85', '2'}) conf: 0.4053575941369725
frozenset({'63', '85'}) --> frozenset({'2', '36'}) conf: 0.5575364667747164
frozenset({'85', '36'}) --> frozenset({'63', '2'}) conf: 0.40399295361127424
frozenset({'63', '36'}) --> frozenset({'85', '2'}) conf: 0.6577437858508605
frozenset({'36'}) --> frozenset({'63', '85', '2'}) conf: 0.40399295361127424
frozenset({'63'}) --> frozenset({'85', '2', '36'}) conf: 0.5575364667747164
frozenset({'85', '86'}) --> frozenset({'63', '2'}) conf: 0.40484603735487124
frozenset({'63', '86'}) --> frozenset({'85', '2'}) conf: 0.6762225969645869
frozenset({'63', '85'}) --> frozenset({'86', '2'}) conf: 0.6499189627228524
frozenset({'86'}) --> frozenset({'63', '85', '2'}) conf: 0.40484603735487124
frozenset({'63'}) --> frozenset({'86', '85', '2'}) conf: 0.6499189627228524
frozenset({'63', '86'}) --> frozenset({'34', '2'}) conf: 0.6762225969645869
frozense

frozenset({'85', '86'}) --> frozenset({'34', '28', '2'}) conf: 0.40585562847046946
frozenset({'34', '28'}) --> frozenset({'86', '85', '2'}) conf: 0.9640287769784172
frozenset({'28', '86'}) --> frozenset({'34', '85', '2'}) conf: 0.9663461538461537
frozenset({'28', '85'}) --> frozenset({'34', '86', '2'}) conf: 0.91156462585034
frozenset({'34'}) --> frozenset({'28', '2', '85', '86'}) conf: 0.40636846095526913
frozenset({'86'}) --> frozenset({'28', '2', '34', '85'}) conf: 0.40585562847046946
frozenset({'28'}) --> frozenset({'2', '34', '85', '86'}) conf: 0.91156462585034
frozenset({'34', '59', '86'}) --> frozenset({'28', '2'}) conf: 0.5313001605136437
frozenset({'34', '28', '86'}) --> frozenset({'59', '2'}) conf: 0.7956730769230769
frozenset({'28', '59', '86'}) --> frozenset({'34', '2'}) conf: 0.9706744868035191
frozenset({'34', '28', '59'}) --> frozenset({'86', '2'}) conf: 0.9706744868035191
frozenset({'34', '59'}) --> frozenset({'86', '28', '2'}) conf: 0.5313001605136437
frozenset({'59', 

frozenset({'63', '86'}) --> frozenset({'90', '59', '2'}) conf: 0.5556492411467118
frozenset({'63', '90'}) --> frozenset({'86', '59', '2'}) conf: 0.5862989323843417
frozenset({'63', '59'}) --> frozenset({'86', '90', '2'}) conf: 0.6342637151106834
frozenset({'59', '86'}) --> frozenset({'63', '90', '2'}) conf: 0.528892455858748
frozenset({'90', '59'}) --> frozenset({'63', '86', '2'}) conf: 0.5565878378378379
frozenset({'63'}) --> frozenset({'90', '2', '59', '86'}) conf: 0.534035656401945
frozenset({'59'}) --> frozenset({'90', '2', '63', '86'}) conf: 0.509273570324575
frozenset({'63', '90', '85'}) --> frozenset({'59', '2'}) conf: 0.6290035587188613
frozenset({'63', '90', '59'}) --> frozenset({'85', '2'}) conf: 0.7465681098204857
frozenset({'63', '59', '85'}) --> frozenset({'90', '2'}) conf: 0.6804619826756497
frozenset({'90', '59', '85'}) --> frozenset({'63', '2'}) conf: 0.5971283783783784
frozenset({'63', '90'}) --> frozenset({'59', '85', '2'}) conf: 0.6290035587188613
frozenset({'63', '8

frozenset({'59', '93'}) --> frozenset({'34', '39', '2'}) conf: 0.7117903930131004
frozenset({'39', '93'}) --> frozenset({'34', '59', '2'}) conf: 0.7855421686746988
frozenset({'59'}) --> frozenset({'93', '2', '34', '39'}) conf: 0.5038639876352395
frozenset({'39'}) --> frozenset({'93', '2', '34', '59'}) conf: 0.46471846044191023
frozenset({'93'}) --> frozenset({'2', '34', '39', '59'}) conf: 0.657258064516129
frozenset({'34', '63', '59'}) --> frozenset({'93', '2'}) conf: 0.639757820383451
frozenset({'34', '63', '93'}) --> frozenset({'59', '2'}) conf: 0.773170731707317
frozenset({'63', '59', '93'}) --> frozenset({'34', '2'}) conf: 0.7620192307692307
frozenset({'34', '59', '93'}) --> frozenset({'63', '2'}) conf: 0.7304147465437788
frozenset({'34', '63'}) --> frozenset({'59', '93', '2'}) conf: 0.5345699831365937
frozenset({'63', '59'}) --> frozenset({'34', '93', '2'}) conf: 0.6102021174205967
frozenset({'34', '59'}) --> frozenset({'63', '93', '2'}) conf: 0.5088282504012841
frozenset({'63', '

...

frozenset({'23', '39', '93', '86'}) --> frozenset({'34', '2', '36'}) conf: 0.8725212464589236
frozenset({'23', '39', '93', '36'}) --> frozenset({'34', '86', '2'}) conf: 0.8725212464589236
frozenset({'34', '23', '39', '93'}) --> frozenset({'86', '2', '36'}) conf: 0.8725212464589236
frozenset({'34', '23', '86'}) --> frozenset({'93', '2', '36', '39'}) conf: 0.7298578199052134
frozenset({'34', '23', '36'}) --> frozenset({'93', '2', '39', '86'}) conf: 0.7530562347188264
frozenset({'34', '39', '86'}) --> frozenset({'23', '93', '2', '36'}) conf: 0.4561273602369493
frozenset({'34', '39', '36'}) --> frozenset({'23', '93', '2', '86'}) conf: 0.5669581224114129
frozenset({'34', '23', '39'}) --> frozenset({'93', '2', '36', '86'}) conf: 0.8169761273209549
frozenset({'23', '86', '36'}) --> frozenset({'93', '2', '34', '39'}) conf: 0.7530562347188264
frozenset({'39', '86', '36'}) --> frozenset({'23', '93', '2', '34'}) conf: 0.5646196150320807
frozenset({'23', '39', '86'}) --> frozenset({'93', '2', '36'

frozenset({'59', '86', '36'}) --> frozenset({'23', '2', '34', '85'}) conf: 0.6275992438563328
frozenset({'23', '59', '86'}) --> frozenset({'2', '36', '34', '85'}) conf: 0.8217821782178218
frozenset({'23', '59', '36'}) --> frozenset({'2', '34', '85', '86'}) conf: 0.8491048593350384
frozenset({'34', '59', '85'}) --> frozenset({'23', '2', '36', '86'}) conf: 0.5329052969502408
frozenset({'59', '85', '86'}) --> frozenset({'23', '2', '36', '34'}) conf: 0.5329052969502408
frozenset({'59', '85', '36'}) --> frozenset({'23', '2', '34', '86'}) conf: 0.6003616636528029
frozenset({'23', '59', '85'}) --> frozenset({'2', '36', '34', '86'}) conf: 0.8217821782178218
frozenset({'34', '23'}) --> frozenset({'59', '85', '2', '36', '86'}) conf: 0.7867298578199052
frozenset({'34', '36'}) --> frozenset({'59', '85', '23', '2', '86'}) conf: 0.4023023326264768
frozenset({'23', '36'}) --> frozenset({'59', '85', '2', '34', '86'}) conf: 0.8117359413202935
frozenset({'86', '36'}) --> frozenset({'59', '85', '23', '2'

frozenset({'63', '23', '39', '85'}) --> frozenset({'2', '36', '34', '86'}) conf: 0.9194029850746269
frozenset({'34', '23', '39', '85'}) --> frozenset({'2', '36', '63', '86'}) conf: 0.8169761273209549
frozenset({'34', '23', '63'}) --> frozenset({'39', '85', '2', '36', '86'}) conf: 0.8105263157894738
frozenset({'34', '63', '36'}) --> frozenset({'39', '85', '23', '2', '86'}) conf: 0.6172344689378758
frozenset({'34', '63', '86'}) --> frozenset({'39', '85', '23', '2', '36'}) conf: 0.5193929173693087
frozenset({'34', '63', '85'}) --> frozenset({'39', '23', '2', '36', '86'}) conf: 0.5193929173693087
frozenset({'63', '85', '86'}) --> frozenset({'39', '23', '2', '36', '34'}) conf: 0.5193929173693087
frozenset({'23', '86', '36'}) --> frozenset({'39', '85', '2', '34', '63'}) conf: 0.7530562347188264
frozenset({'63', '23', '36'}) --> frozenset({'39', '85', '2', '34', '86'}) conf: 0.8392370572207085
frozenset({'63', '86', '36'}) --> frozenset({'39', '85', '23', '2', '34'}) conf: 0.6172344689378758


frozenset({'34', '39', '86'}) --> frozenset({'93', '85', '23', '2', '36'}) conf: 0.4561273602369493
frozenset({'34', '39', '36'}) --> frozenset({'93', '85', '23', '2', '86'}) conf: 0.5669581224114129
frozenset({'39', '86', '36'}) --> frozenset({'93', '85', '23', '2', '34'}) conf: 0.5646196150320807
frozenset({'34', '39', '85'}) --> frozenset({'93', '23', '2', '36', '86'}) conf: 0.4561273602369493
frozenset({'39', '85', '86'}) --> frozenset({'93', '23', '2', '36', '34'}) conf: 0.4546125461254613
frozenset({'39', '85', '36'}) --> frozenset({'93', '23', '2', '34', '86'}) conf: 0.5408252853380159
frozenset({'23', '39', '85'}) --> frozenset({'93', '2', '36', '34', '86'}) conf: 0.8169761273209549
frozenset({'23', '86', '36'}) --> frozenset({'93', '39', '85', '2', '34'}) conf: 0.7530562347188264
frozenset({'23', '85', '36'}) --> frozenset({'93', '39', '2', '34', '86'}) conf: 0.7530562347188264
frozenset({'23', '39', '36'}) --> frozenset({'93', '85', '2', '34', '86'}) conf: 0.8169761273209549


frozenset({'93', '86', '36'}) --> frozenset({'39', '59', '85', '2', '34'}) conf: 0.7493917274939174
frozenset({'93', '85', '36'}) --> frozenset({'39', '59', '2', '34', '86'}) conf: 0.7080459770114943
frozenset({'59', '93', '36'}) --> frozenset({'39', '85', '2', '34', '86'}) conf: 0.7421686746987953
frozenset({'93', '85', '86'}) --> frozenset({'39', '59', '2', '36', '34'}) conf: 0.652542372881356
frozenset({'59', '93', '86'}) --> frozenset({'39', '85', '2', '36', '34'}) conf: 0.7096774193548387
frozenset({'59', '93', '85'}) --> frozenset({'39', '2', '36', '34', '86'}) conf: 0.6724890829694324
frozenset({'34', '39', '93'}) --> frozenset({'59', '85', '2', '36', '86'}) conf: 0.7877237851662405
frozenset({'39', '93', '36'}) --> frozenset({'59', '85', '2', '34', '86'}) conf: 0.8126649076517152
frozenset({'39', '93', '86'}) --> frozenset({'59', '85', '2', '36', '34'}) conf: 0.7877237851662405
frozenset({'39', '93', '85'}) --> frozenset({'59', '2', '36', '34', '86'}) conf: 0.7421686746987953
f

In [7]:
L, suppData = apriori(mushDataSet, minSupport=0.3)
rules = generateRules(L, suppData, minConf=0.5)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'28'}) --> frozenset({'2'}) conf: 0.9659863945578231
frozenset({'53'}) --> frozenset({'2'}) conf: 0.5625
frozenset({'23'}) --> frozenset({'2'}) conf: 0.8151658767772512
frozenset({'34'}) --> frozenset({'2'}) conf: 0.5074551427849381
frozenset({'59'}) --> frozenset({'2'}) conf: 0.7032457496136012
frozenset({'63'}) --> frozenset({'2'}) conf: 0.6888168557536466
frozenset({'67'}) --> frozenset({'2'}) conf: 0.6164874551971327
frozenset({'76'}) --> frozenset({'2'}) conf: 0.6167883211678832
frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
frozenset({'86'}) --> frozenset({'2'}) conf: 0.5068147400302877
frozenset({'93'}) --> frozenset({'2'}) conf: 0.7943548387096774
frozenset({'39'}) --> frozenset({'2'}) conf: 0.6985032074126871
frozenset({'53'}) --> frozenset({'39', '2'}) conf: 0.5416666666666666
frozenset({'53'}) --> frozenset({'90', '2'}) conf: 0.5625
frozenset({'53'}) --> frozenset({'86', '2'}) conf: 0.5625
frozenset({'53'}) --> frozenset({'85', '2'}) conf: 0.5625
f

frozenset({'39', '59'}) --> frozenset({'23', '2'}) conf: 0.7394209354120267
frozenset({'23', '59'}) --> frozenset({'39', '2'}) conf: 0.8217821782178218
frozenset({'23', '39'}) --> frozenset({'59', '2'}) conf: 0.8806366047745359
frozenset({'59'}) --> frozenset({'23', '39', '2'}) conf: 0.5131375579598145
frozenset({'23'}) --> frozenset({'39', '59', '2'}) conf: 0.7867298578199052
frozenset({'23', '85'}) --> frozenset({'39', '2'}) conf: 0.7867298578199052
frozenset({'23', '39'}) --> frozenset({'85', '2'}) conf: 0.8806366047745359
frozenset({'23'}) --> frozenset({'39', '85', '2'}) conf: 0.7867298578199052
frozenset({'23', '86'}) --> frozenset({'39', '2'}) conf: 0.7867298578199052
frozenset({'23', '39'}) --> frozenset({'86', '2'}) conf: 0.8806366047745359
frozenset({'23'}) --> frozenset({'86', '39', '2'}) conf: 0.7867298578199052
frozenset({'39', '93'}) --> frozenset({'23', '2'}) conf: 0.7421686746987953
frozenset({'23', '39'}) --> frozenset({'93', '2'}) conf: 0.8169761273209549
frozenset({'

frozenset({'63', '59', '85'}) --> frozenset({'39', '2'}) conf: 0.7025986525505293
frozenset({'63', '39', '85'}) --> frozenset({'59', '2'}) conf: 0.8588235294117648
frozenset({'63', '39', '59'}) --> frozenset({'85', '2'}) conf: 0.9530026109660575
frozenset({'39', '59', '85'}) --> frozenset({'63', '2'}) conf: 0.8129175946547884
frozenset({'63', '85'}) --> frozenset({'39', '59', '2'}) conf: 0.5915721231766612
frozenset({'63', '59'}) --> frozenset({'39', '85', '2'}) conf: 0.7025986525505293
frozenset({'59', '85'}) --> frozenset({'63', '39', '2'}) conf: 0.5641421947449768
frozenset({'63', '39'}) --> frozenset({'59', '85', '2'}) conf: 0.8588235294117648
frozenset({'39', '85'}) --> frozenset({'63', '59', '2'}) conf: 0.5203136136849609
frozenset({'39', '59'}) --> frozenset({'63', '85', '2'}) conf: 0.8129175946547884
frozenset({'63'}) --> frozenset({'2', '39', '59', '85'}) conf: 0.5915721231766612
frozenset({'59'}) --> frozenset({'2', '63', '39', '85'}) conf: 0.5641421947449768
frozenset({'39'}

frozenset({'59'}) --> frozenset({'2', '63', '85', '86'}) conf: 0.5664605873261206
frozenset({'63', '59', '36'}) --> frozenset({'39', '2'}) conf: 0.7217391304347825
frozenset({'63', '39', '36'}) --> frozenset({'59', '2'}) conf: 0.924791086350975
frozenset({'63', '39', '59'}) --> frozenset({'2', '36'}) conf: 0.8668407310704962
frozenset({'39', '59', '36'}) --> frozenset({'63', '2'}) conf: 0.8668407310704962
frozenset({'63', '36'}) --> frozenset({'39', '59', '2'}) conf: 0.6347992351816444
frozenset({'63', '59'}) --> frozenset({'39', '2', '36'}) conf: 0.6390760346487007
frozenset({'59', '36'}) --> frozenset({'63', '39', '2'}) conf: 0.6003616636528029
frozenset({'63', '39'}) --> frozenset({'59', '2', '36'}) conf: 0.7811764705882354
frozenset({'39', '36'}) --> frozenset({'63', '59', '2'}) conf: 0.5829675153643548
frozenset({'39', '59'}) --> frozenset({'63', '2', '36'}) conf: 0.7394209354120267
frozenset({'63'}) --> frozenset({'2', '36', '39', '59'}) conf: 0.5380875202593193
frozenset({'59'})

frozenset({'23', '36'}) --> frozenset({'34', '93', '2'}) conf: 0.7530562347188264
frozenset({'34', '93'}) --> frozenset({'23', '2', '36'}) conf: 0.652542372881356
frozenset({'93', '36'}) --> frozenset({'34', '23', '2'}) conf: 0.7080459770114943
frozenset({'23', '93'}) --> frozenset({'34', '2', '36'}) conf: 0.7738693467336684
frozenset({'23'}) --> frozenset({'93', '2', '36', '34'}) conf: 0.7298578199052134
frozenset({'93'}) --> frozenset({'23', '2', '36', '34'}) conf: 0.6209677419354839
frozenset({'23', '86', '36'}) --> frozenset({'93', '2'}) conf: 0.7530562347188264
frozenset({'93', '86', '36'}) --> frozenset({'23', '2'}) conf: 0.7493917274939174
frozenset({'23', '93', '86'}) --> frozenset({'2', '36'}) conf: 0.7738693467336684
frozenset({'23', '93', '36'}) --> frozenset({'86', '2'}) conf: 0.8
frozenset({'23', '86'}) --> frozenset({'93', '2', '36'}) conf: 0.7298578199052134
frozenset({'23', '36'}) --> frozenset({'86', '93', '2'}) conf: 0.7530562347188264
frozenset({'93', '86'}) --> froz

...

frozenset({'63', '86', '36'}) --> frozenset({'23', '2', '34', '39'}) conf: 0.6172344689378758
frozenset({'63', '23', '86'}) --> frozenset({'2', '36', '34', '39'}) conf: 0.8105263157894738
frozenset({'23', '86', '36'}) --> frozenset({'2', '34', '39', '63'}) conf: 0.7530562347188264
frozenset({'63', '23', '36'}) --> frozenset({'2', '34', '39', '86'}) conf: 0.8392370572207085
frozenset({'34', '23', '86'}) --> frozenset({'2', '36', '63', '39'}) conf: 0.7298578199052134
frozenset({'34', '23', '36'}) --> frozenset({'2', '63', '39', '86'}) conf: 0.7530562347188264
frozenset({'34', '39', '63'}) --> frozenset({'23', '2', '36', '86'}) conf: 0.7680798004987532
frozenset({'63', '39', '86'}) --> frozenset({'23', '2', '36', '34'}) conf: 0.7680798004987532
frozenset({'39', '86', '36'}) --> frozenset({'23', '2', '34', '63'}) conf: 0.5646196150320807
frozenset({'63', '39', '36'}) --> frozenset({'23', '2', '34', '86'}) conf: 0.8579387186629528
frozenset({'34', '39', '36'}) --> frozenset({'23', '2', '63'

frozenset({'34', '23', '59', '36'}) --> frozenset({'86', '85', '2'}) conf: 0.8491048593350384
frozenset({'23', '59', '86', '36'}) --> frozenset({'34', '85', '2'}) conf: 0.8491048593350384
frozenset({'34', '59', '85', '86'}) --> frozenset({'23', '2', '36'}) conf: 0.5329052969502408
frozenset({'34', '59', '85', '36'}) --> frozenset({'23', '86', '2'}) conf: 0.6275992438563328
frozenset({'59', '85', '86', '36'}) --> frozenset({'34', '23', '2'}) conf: 0.6275992438563328
frozenset({'23', '59', '85', '86'}) --> frozenset({'34', '2', '36'}) conf: 0.8217821782178218
frozenset({'23', '59', '85', '36'}) --> frozenset({'34', '86', '2'}) conf: 0.8491048593350384
frozenset({'34', '23', '59', '85'}) --> frozenset({'86', '2', '36'}) conf: 0.8217821782178218
frozenset({'34', '23', '86'}) --> frozenset({'2', '36', '59', '85'}) conf: 0.7867298578199052
frozenset({'34', '23', '36'}) --> frozenset({'2', '59', '85', '86'}) conf: 0.8117359413202935
frozenset({'34', '23', '85'}) --> frozenset({'2', '36', '59'

frozenset({'23', '39', '36'}) --> frozenset({'85', '2', '34', '63', '86'}) conf: 0.8169761273209549
frozenset({'34', '39', '36'}) --> frozenset({'85', '23', '2', '63', '86'}) conf: 0.5669581224114129
frozenset({'34', '23', '39'}) --> frozenset({'85', '2', '36', '63', '86'}) conf: 0.8169761273209549
frozenset({'63', '39', '85'}) --> frozenset({'23', '2', '36', '34', '86'}) conf: 0.7247058823529413
frozenset({'39', '85', '36'}) --> frozenset({'23', '2', '34', '63', '86'}) conf: 0.5408252853380159
frozenset({'23', '39', '85'}) --> frozenset({'2', '36', '34', '63', '86'}) conf: 0.8169761273209549
frozenset({'63', '23'}) --> frozenset({'39', '85', '2', '36', '34', '86'}) conf: 0.8105263157894738
frozenset({'34', '23'}) --> frozenset({'39', '85', '2', '36', '63', '86'}) conf: 0.7298578199052134
frozenset({'34', '63'}) --> frozenset({'39', '85', '23', '2', '36', '86'}) conf: 0.5193929173693087
frozenset({'63', '36'}) --> frozenset({'39', '85', '23', '2', '34', '86'}) conf: 0.5889101338432123


frozenset({'93', '59', '85', '36', '34'}) --> frozenset({'23', '39', '2'}) conf: 0.7877237851662405
frozenset({'93', '59', '85', '23', '34'}) --> frozenset({'39', '2', '36'}) conf: 0.8105263157894738
frozenset({'93', '59', '85', '23', '36'}) --> frozenset({'34', '39', '2'}) conf: 0.8392370572207085
frozenset({'93', '39', '23', '36', '34'}) --> frozenset({'59', '85', '2'}) conf: 0.8725212464589236
frozenset({'93', '39', '85', '36', '34'}) --> frozenset({'23', '59', '2'}) conf: 0.867605633802817
frozenset({'93', '39', '85', '23', '34'}) --> frozenset({'59', '2', '36'}) conf: 0.8725212464589236
frozenset({'93', '39', '85', '23', '36'}) --> frozenset({'34', '59', '2'}) conf: 0.8725212464589236
frozenset({'93', '39', '59', '36', '34'}) --> frozenset({'23', '85', '2'}) conf: 0.9194029850746269
frozenset({'93', '39', '59', '23', '34'}) --> frozenset({'85', '2', '36'}) conf: 0.9194029850746269
frozenset({'93', '39', '59', '23', '36'}) --> frozenset({'34', '85', '2'}) conf: 0.9194029850746269
f

frozenset({'23', '39', '93', '85'}) --> frozenset({'59', '2', '36', '34', '86'}) conf: 0.8725212464589236
frozenset({'34', '39', '93', '59'}) --> frozenset({'85', '23', '2', '36', '86'}) conf: 0.8725212464589236
frozenset({'39', '93', '59', '86'}) --> frozenset({'85', '23', '2', '36', '34'}) conf: 0.8725212464589236
frozenset({'39', '93', '59', '36'}) --> frozenset({'85', '23', '2', '34', '86'}) conf: 0.8579387186629528
frozenset({'23', '39', '93', '59'}) --> frozenset({'85', '2', '36', '34', '86'}) conf: 0.9194029850746269
frozenset({'85', '39', '93', '59'}) --> frozenset({'23', '2', '36', '34', '86'}) conf: 0.8169761273209549
frozenset({'34', '23', '36'}) --> frozenset({'93', '39', '59', '85', '2', '86'}) conf: 0.7530562347188264
frozenset({'34', '23', '86'}) --> frozenset({'93', '39', '59', '85', '2', '36'}) conf: 0.7298578199052134
frozenset({'23', '86', '36'}) --> frozenset({'93', '39', '59', '85', '2', '34'}) conf: 0.7530562347188264
frozenset({'34', '23', '85'}) --> frozenset({'

In [8]:
L, suppData = apriori(mushDataSet, minSupport=0.4)
rules = generateRules(L, suppData, minConf=0.3)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'28'}) --> frozenset({'2'}) conf: 0.9659863945578231
frozenset({'34'}) --> frozenset({'2'}) conf: 0.5074551427849381
frozenset({'59'}) --> frozenset({'2'}) conf: 0.7032457496136012
frozenset({'63'}) --> frozenset({'2'}) conf: 0.6888168557536466
frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
frozenset({'86'}) --> frozenset({'2'}) conf: 0.5068147400302877
frozenset({'90'}) --> frozenset({'2'}) conf: 0.4914529914529915
frozenset({'39'}) --> frozenset({'2'}) conf: 0.6985032074126871
frozenset({'85'}) --> frozenset({'28', '2'}) conf: 0.4194977843426883
frozenset({'28'}) --> frozenset({'85', '2'}) conf: 0.9659863945578231
frozenset({'86'}) --> frozenset({'39', '2'}) conf: 0.47046945986875316
frozenset({'39'}) --> frozenset({'86', '2'}) conf: 0.6642908054169637
frozenset({'85'}) --> frozenset({'39', '2'}) conf: 0.48252092565238797
frozenset({'39'}) --> frozenset({'85', '2'}) conf: 0.6985032074126871
frozenset({'59'}) --> frozenset({'39', '2'}) conf: 0.65224111282843

In [9]:
L, suppData = apriori(mushDataSet, minSupport=0.4)
rules = generateRules(L, suppData, minConf=0.4)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'28'}) --> frozenset({'2'}) conf: 0.9659863945578231
frozenset({'34'}) --> frozenset({'2'}) conf: 0.5074551427849381
frozenset({'59'}) --> frozenset({'2'}) conf: 0.7032457496136012
frozenset({'63'}) --> frozenset({'2'}) conf: 0.6888168557536466
frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
frozenset({'86'}) --> frozenset({'2'}) conf: 0.5068147400302877
frozenset({'90'}) --> frozenset({'2'}) conf: 0.4914529914529915
frozenset({'39'}) --> frozenset({'2'}) conf: 0.6985032074126871
frozenset({'85'}) --> frozenset({'28', '2'}) conf: 0.4194977843426883
frozenset({'28'}) --> frozenset({'85', '2'}) conf: 0.9659863945578231
frozenset({'86'}) --> frozenset({'39', '2'}) conf: 0.47046945986875316
frozenset({'39'}) --> frozenset({'86', '2'}) conf: 0.6642908054169637
frozenset({'85'}) --> frozenset({'39', '2'}) conf: 0.48252092565238797
frozenset({'39'}) --> frozenset({'85', '2'}) conf: 0.6985032074126871
frozenset({'59'}) --> frozenset({'39', '2'}) conf: 0.65224111282843

In [10]:
L, suppData = apriori(mushDataSet, minSupport=0.4)
rules = generateRules(L, suppData, minConf=0.5)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'28'}) --> frozenset({'2'}) conf: 0.9659863945578231
frozenset({'34'}) --> frozenset({'2'}) conf: 0.5074551427849381
frozenset({'59'}) --> frozenset({'2'}) conf: 0.7032457496136012
frozenset({'63'}) --> frozenset({'2'}) conf: 0.6888168557536466
frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
frozenset({'86'}) --> frozenset({'2'}) conf: 0.5068147400302877
frozenset({'39'}) --> frozenset({'2'}) conf: 0.6985032074126871
frozenset({'28'}) --> frozenset({'85', '2'}) conf: 0.9659863945578231
frozenset({'39'}) --> frozenset({'86', '2'}) conf: 0.6642908054169637
frozenset({'39'}) --> frozenset({'85', '2'}) conf: 0.6985032074126871
frozenset({'59'}) --> frozenset({'39', '2'}) conf: 0.6522411128284389
frozenset({'39'}) --> frozenset({'59', '2'}) conf: 0.601568068424804
frozenset({'59'}) --> frozenset({'90', '2'}) conf: 0.6321483771251932
frozenset({'39'}) --> frozenset({'90', '2'}) conf: 0.6044191019244476
frozenset({'86'}) --> frozenset({'85', '2'}) conf: 0.50681474003

In [11]:
L, suppData = apriori(mushDataSet, minSupport=0.5)
rules = generateRules(L, suppData, minConf=0.3)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
1


In [12]:
L, suppData = apriori(mushDataSet, minSupport=0.5)
rules = generateRules(L, suppData, minConf=0.4)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
1


In [13]:
L, suppData = apriori(mushDataSet, minSupport=0.5)
rules = generateRules(L, suppData, minConf=0.5)
i = 0
for qian, hou, conf in rules:
    if '2' in hou: # 有毒
        print(qian, '-->', hou, 'conf:', conf)
        i += 1
print(i)

frozenset({'85'}) --> frozenset({'2'}) conf: 0.517971442639094
1


接下来你需要观察一下这些特征，以便知道了解野蘑菇的那些方面。如果看到其中任何一个特征，那么这些蘑菇就不要吃了。

当然最后还是要声明一下：

    尽管上述这些特征在毒蘑菇中很普遍，但是没有这些特征并不意味着该蘑菇就是可食用的。如果吃错了蘑菇，你可能会因此而丧命。